In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

# Hindi Profanity Filter (BOLO MAGAR PYAR SE)

**MANUALLY CURATED HINDI PROFANITY DATASET**

In [1]:
import kagglehub

# Download latest version
path = kagglehub.dataset_download("shadow4ever/top-112-hindi-swear-words")

print("Path to dataset files:", path)

Path to dataset files: /kaggle/input/top-112-hindi-swear-words


In [2]:
import pandas as pd

!pip install SpeechRecognition

!pip install pyttsx3

!pip install SimpleAudio


!pip install sounddevice


import speech_recognition as sr
!pip install gtts

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 56.1 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 53.7 MB/s eta 0:00:0000:01
  Preparing metadata (setup.py) ... done
  Created wheel for SimpleAudio: filename=simpleaudio-1.0.4-cp310-cp310-linux_x86_64.whl size=2054404 sha256=9cd71781f3201fc70612148bec0c85433c20446a4051bfe41e6142a11e2844c5
  Stored in directory: /root/.cache/pip/wheels/10/70/ed/8c41675109565c2c65c3ac40d20859fc9d3f93a8efbb11d1c7
Successfully built SimpleAudio


# RULE BASED METHOD

In [3]:
import os
import pandas as pd
import speech_recognition as sr
from pydub import AudioSegment
from gtts import gTTS
import numpy as np
from IPython.display import Audio, display

def load_hindi_profanity_list(dataset_path="/kaggle/input/top-112-hindi-swear-words/hindi top 150 swear words .csv"):
    """Load Hindi profanity list from the dataset."""
    try:
        df = pd.read_csv(dataset_path)
        # Assuming cuss words are in the second column (index 1)
        profanity_list = set(df.iloc[:, 1].dropna().str.strip())
        print(f"Loaded {len(profanity_list)} Hindi profane words/phrases.")
        return profanity_list
    except Exception as e:
        print(f"Error loading Hindi profanity dataset: {e}")
        return set()

def convert_to_wav(file_path, output_dir="/kaggle/working"):
    """Convert MP3/M4A to WAV and return raw audio path."""
    os.makedirs(output_dir, exist_ok=True)
    file_name, ext = os.path.splitext(os.path.basename(file_path))
    output_path = os.path.join(output_dir, f"{file_name}_raw.wav")
    if ext.lower() != ".wav":
        audio = AudioSegment.from_file(file_path, format=ext[1:])
        audio = audio.set_channels(1).set_frame_rate(16000)
        audio.export(output_path, format="wav")
    return output_path

def create_beep_sound(duration=500, freq=1000):
    """Generate a simple beep sound."""
    sample_rate = 44100
    t = np.linspace(0, duration / 1000, int(sample_rate * duration / 1000), False)
    beep_signal = 0.5 * np.sin(2 * np.pi * freq * t)
    audio_data = (beep_signal * 32767).astype(np.int16)
    return AudioSegment(audio_data.tobytes(), frame_rate=sample_rate, sample_width=2, channels=1)

def transcribe_hindi_audio(audio_file, output_dir="/kaggle/working"):
    """Transcribe Hindi audio file and return raw text and WAV path."""
    wav_file = convert_to_wav(audio_file, output_dir)
    recognizer = sr.Recognizer()
    try:
        with sr.AudioFile(wav_file) as source:
            audio = recognizer.record(source)
        raw_text = recognizer.recognize_google(audio, language='hi-IN')
        return raw_text, wav_file
    except Exception as e:
        print(f"Error transcribing Hindi audio: {e}")
        return None, None

def censor_hindi_text(text, profanity_list):
    """Censor text with stars and [BEEP], handling multi-word profanity from the list."""
    words = text.split()
    display_words = words.copy()
    audio_words = words.copy()
    i = 0

    while i < len(words):
        # Check 3-word phrase
        if i + 2 < len(words):
            phrase_3 = " ".join(words[i:i+3])
            if phrase_3 in profanity_list:
                print(f"Flagged profane phrase: {phrase_3}")
                censored_phrase = " ".join([w[0] + "*" * (len(w) - 1) if len(w) > 1 else w for w in words[i:i+3]])
                display_words[i:i+3] = [censored_phrase]
                audio_words[i:i+3] = ["[BEEP]"]
                i += 3
                continue

        # Check 2-word phrase
        if i + 1 < len(words):
            phrase_2 = " ".join(words[i:i+2])
            if phrase_2 in profanity_list:
                print(f"Flagged profane phrase: {phrase_2}")
                censored_phrase = " ".join([w[0] + "*" * (len(w) - 1) if len(w) > 1 else w for w in words[i:i+2]])
                display_words[i:i+2] = [censored_phrase]
                audio_words[i:i+2] = ["[BEEP]"]
                i += 2
                continue

        # Check single word
        word = words[i]
        if word in profanity_list:
            print(f"Flagged profane word: {word}")
            censored_word = word[0] + "*" * (len(word) - 1) if len(word) > 1 else word
            display_words[i] = censored_word
            audio_words[i] = "[BEEP]"
        i += 1

    display_text = " ".join(" ".join([w] if " " not in w else [w]) for w in display_words)
    audio_text = " ".join(audio_words)
    return display_text, audio_text

def generate_and_display_hindi_audio(input_type, original_text, modified_text, raw_wav_file=None, output_dir="/kaggle/working"):
    """Generate and display raw and censored Hindi audio."""
    base_name = os.path.splitext(os.path.basename(raw_wav_file))[0] if input_type == 'audio' else "generated_hindi"
    raw_audio_wav = os.path.join(output_dir, f"{base_name}_raw.wav")
    censored_audio_wav = os.path.join(output_dir, f"{base_name}_censored.wav")

    if input_type.lower() == 'text':
        print("Generating Raw Hindi Audio Playback:")
        tts_raw = gTTS(text=original_text, lang='hi', slow=False)
        tts_raw.save("/kaggle/working/temp_raw.mp3")
        AudioSegment.from_mp3("/kaggle/working/temp_raw.mp3").export(raw_audio_wav, format="wav")
        os.remove("/kaggle/working/temp_raw.mp3")
        display(Audio(raw_audio_wav))
    elif input_type.lower() == 'audio' and raw_wav_file:
        print("Raw Hindi Audio Playback:")
        display(Audio(raw_wav_file))

    beep = create_beep_sound() if not os.path.exists("/kaggle/input/beep-sound/beep.wav") else AudioSegment.from_file("/kaggle/input/beep-sound/beep.wav")
    segments = modified_text.split("[BEEP]")
    final_audio = AudioSegment.empty()
    temp_file = os.path.join(output_dir, "temp.mp3")

    for i, segment in enumerate(segments):
        if segment.strip():
            tts = gTTS(text=segment.strip(), lang='hi', slow=False)
            tts.save(temp_file)
            segment_audio = AudioSegment.from_mp3(temp_file)
            final_audio += segment_audio
        if i < len(segments) - 1:
            final_audio += beep

    final_audio.export(censored_audio_wav, format="wav")
    print("Censored Hindi Audio Playback:")
    display(Audio(censored_audio_wav))
    if os.path.exists(temp_file):
        os.remove(temp_file)
    return raw_audio_wav, censored_audio_wav

def process_hindi_input(input_data, is_audio=True, output_dir="/kaggle/working"):
    """Process Hindi audio or text input, censoring based on the profanity list."""
    os.makedirs(output_dir, exist_ok=True)
    profanity_list = load_hindi_profanity_list()

    if is_audio:
        raw_text, raw_wav = transcribe_hindi_audio(input_data, output_dir)
        if raw_text is None:
            return None
    else:
        raw_text = input_data
        raw_wav = None

    display_text, audio_text = censor_hindi_text(raw_text, profanity_list)
    print(f"Input Text: {raw_text}")
    print(f"Modified Text (for audio): {audio_text}")

    raw_audio_path, censored_audio_path = generate_and_display_hindi_audio(
        'audio' if is_audio else 'text', raw_text, audio_text, raw_wav, output_dir
    )

    print("\nTranscript:")
    print(display_text)
    print(f"Raw Audio Sample: {raw_audio_path}")
    print(f"Censored Audio Sample: {censored_audio_path}")
    return raw_audio_path, censored_audio_path

# Example usage
if __name__ == "__main__":
    input_type = input("Enter input type ('text' or 'audio'): ").strip().lower()
    if input_type == 'audio':
        input_data = input("Enter Hindi audio file path (MP3/WAV/M4A): ").strip()
        process_hindi_input(input_data, is_audio=True)
    elif input_type == 'text':
        input_data = input("Paste your Hindi text here: ").strip()
        process_hindi_input(input_data, is_audio=False)
    else:
        print("Invalid input type. Use 'text' or 'audio'.")

Enter input type ('text' or 'audio'):  text
Paste your Hindi text here:  चोदो इस गंदे दिन को, क्या हरामी गड़बड़ है! मेरा वो कमीना बॉस इसे चूस सकता है—सचमुच, क्या भोसड़ी वाला है। ये हरामी नौकरी मुझे पागल कर रही है, और वो चूतिया सहकर्मी मदद नहीं कर रहे। मैं इतना गुस्से में हूँ कि खूनखराबा चिल्ला सकता हूँ। चूतिया ग्राहक, कमीने समय-सीमाएँ, और घटिया वेतन—क्या नरक का भोसड़ी गड़बड़ है!


Loaded 133 Hindi profane words/phrases.
Flagged profane word: चोदो
Flagged profane word: हरामी
Flagged profane word: कमीना
Flagged profane phrase: भोसड़ी वाला
Flagged profane word: हरामी
Flagged profane word: चूतिया
Flagged profane word: चूतिया
Flagged profane word: भोसड़ी
Input Text: चोदो इस गंदे दिन को, क्या हरामी गड़बड़ है! मेरा वो कमीना बॉस इसे चूस सकता है—सचमुच, क्या भोसड़ी वाला है। ये हरामी नौकरी मुझे पागल कर रही है, और वो चूतिया सहकर्मी मदद नहीं कर रहे। मैं इतना गुस्से में हूँ कि खूनखराबा चिल्ला सकता हूँ। चूतिया ग्राहक, कमीने समय-सीमाएँ, और घटिया वेतन—क्या नरक का भोसड़ी गड़बड़ है!
Modified Text (for audio): [BEEP] इस गंदे दिन को, क्या [BEEP] गड़बड़ है! मेरा वो [BEEP] बॉस इसे चूस सकता है—सचमुच, क्या [BEEP] है। ये हरामी [BEEP] मुझे पागल कर रही है, और वो चूतिया [BEEP] मदद नहीं कर रहे। मैं इतना गुस्से में हूँ कि खूनखराबा चिल्ला सकता हूँ। चूतिया [BEEP] कमीने समय-सीमाएँ, और घटिया वेतन—क्या नरक का भोसड़ी [BEEP] है!
Generating Raw Hindi Audio Playback:


Censored Hindi Audio Playback:



Transcript:
च*** इस गंदे दिन को, क्या ह**** गड़बड़ है! मेरा वो क**** बॉस इसे चूस सकता है—सचमुच, क्या भ***** व*** है। ये हरामी ह**** मुझे पागल कर रही है, और वो चूतिया च***** मदद नहीं कर रहे। मैं इतना गुस्से में हूँ कि खूनखराबा चिल्ला सकता हूँ। चूतिया च***** कमीने समय-सीमाएँ, और घटिया वेतन—क्या नरक का भोसड़ी भ***** है!
Raw Audio Sample: /kaggle/working/generated_hindi_raw.wav
Censored Audio Sample: /kaggle/working/generated_hindi_censored.wav


In [4]:
import pandas as pd
from sklearn.metrics import confusion_matrix

def load_hindi_profanity_list(dataset_path="/kaggle/input/top-112-hindi-swear-words/hindi top 150 swear words .csv"):
    """Load Hindi profanity list from the dataset."""
    try:
        df = pd.read_csv(dataset_path)
        profanity_list = set(df.iloc[:, 1].dropna().str.strip())
        print(f"Loaded {len(profanity_list)} Hindi profane words/phrases.")
        return profanity_list
    except Exception as e:
        print(f"Error loading Hindi profanity dataset: {e}")
        return set()

def evaluate_censorship_accuracy(input_text, dataset_path="/kaggle/input/top-112-hindi-swear-words/hindi top 150 swear words .csv"):
    """Calculate accuracy and confusion matrix for Hindi profanity censorship."""
    # Load profanity list (ground truth for profane words)
    profanity_list = load_hindi_profanity_list(dataset_path)
    
    # Split input text into words
    words = input_text.split()
    true_labels = []
    predicted_labels = []
    i = 0

    while i < len(words):
        # Check 3-word phrase
        if i + 2 < len(words):
            phrase_3 = " ".join(words[i:i+3])
            is_profane = phrase_3 in profanity_list
            true_labels.extend([1 if is_profane else 0] * 3)
            predicted_labels.extend([1 if is_profane else 0] * 3)
            if is_profane:
                print(f"Flagged profane phrase: {phrase_3}")
                i += 3
                continue
        # Check 2-word phrase
        if i + 1 < len(words):
            phrase_2 = " ".join(words[i:i+2])
            is_profane = phrase_2 in profanity_list
            true_labels.extend([1 if is_profane else 0] * 2)
            predicted_labels.extend([1 if is_profane else 0] * 2)
            if is_profane:
                print(f"Flagged profane phrase: {phrase_2}")
                i += 2
                continue
        # Check single word
        word = words[i]
        is_profane = word in profanity_list
        true_labels.append(1 if is_profane else 0)
        predicted_labels.append(1 if is_profane else 0)
        if is_profane:
            print(f"Flagged profane word: {word}")
        i += 1

    # Calculate accuracy
    correct = sum(1 for t, p in zip(true_labels, predicted_labels) if t == p)
    accuracy = correct / len(true_labels) if true_labels else 0

    # Generate confusion matrix
    cm = confusion_matrix(true_labels, predicted_labels, labels=[0, 1])
    tn, fp, fn, tp = cm.ravel()

    print("\nCensorship Evaluation:")
    print(f"Total words/phrases evaluated: {len(true_labels)}")
    print(f"Accuracy: {accuracy:.2f}")
    print("Confusion Matrix:")
    print(f"{'':<20} {'Predicted Clean':<15} {'Predicted Censored':<15}")
    print(f"{'Actual Clean':<20} {tn:<15} {fp:<15}")
    print(f"{'Actual Censored':<20} {fn:<15} {tp:<15}")

    return accuracy, cm

# Example usage
if __name__ == "__main__":
    test_input = input("Paste your Hindi text here for evaluation: ").strip()
    accuracy, cm = evaluate_censorship_accuracy(test_input)

Paste your Hindi text here for evaluation:  चोदो इस गंदे दिन को, क्या हरामी गड़बड़ है! मेरा वो कमीना बॉस इसे चूस सकता है—सचमुच, क्या भोसड़ी वाला है। ये हरामी नौकरी मुझे पागल कर रही है, और वो चूतिया सहकर्मी मदद नहीं कर रहे। मैं इतना गुस्से में हूँ कि खूनखराबा चिल्ला सकता हूँ। चूतिया ग्राहक, कमीने समय-सीमाएँ, और घटिया वेतन—क्या नरक का भोसड़ी गड़बड़ है! सुबह से ही यह दिन बहुत गंदा शुरू हुआ। आसमान साफ था, पर मेरा मूड हरामी हो गया। ऑफिस में वो कमीना बॉस मिला, जिसने मेरे काम को चूतिया कहा। मैंने सोचा कि शांत रहूँ, पर उसने चिल्लाकर कहा, “तेरी माँ का!” ये नौकरी मुझे सचमुच दीवार पर चढ़ा रही है। सहकर्मी भी भोसड़ी वाले हैं, कोई मदद नहीं करता। दोपहर तक सब कुछ चोदो जैसा हो गया। ग्राहक हरामी हैं, समय-सीमाएँ कमीने हैं, और वेतन घटिया है। मैं गुस्से से भरा हूँ, चीखना चाहता हूँ। ये दिन नरक का भोसड़ी गड़बड़ बन गया है। नमस्ते कहने का मन नहीं, आज सब गंदा है। ये सुंदर सुबह जल्दी ही हरामी बन गई। मेरा बॉस, वो चूतिया, मुझे सुबह से परेशान कर रहा है। उसने कहा, “ये काम भोसड़ी वाला है!” मैं चुप रहा, पर मन में चोदो

Loaded 133 Hindi profane words/phrases.
Flagged profane word: चोदो
Flagged profane word: हरामी
Flagged profane word: कमीना
Flagged profane phrase: भोसड़ी वाला
Flagged profane word: हरामी
Flagged profane word: चूतिया
Flagged profane word: चूतिया
Flagged profane word: भोसड़ी
Flagged profane word: हरामी
Flagged profane word: कमीना
Flagged profane word: चूतिया
Flagged profane word: भोसड़ी
Flagged profane word: चोदो
Flagged profane word: हरामी
Flagged profane word: भोसड़ी
Flagged profane word: हरामी
Flagged profane phrase: भोसड़ी वाला
Flagged profane word: चोदो
Flagged profane word: हरामी

Censorship Evaluation:
Total words/phrases evaluated: 1460
Accuracy: 1.00
Confusion Matrix:
                     Predicted Clean Predicted Censored
Actual Clean         1439            0              
Actual Censored      0               21             
